In [1]:
from sage.sat.boolean_polynomials import solve as solve_sat
from sage.rings.polynomial.multi_polynomial_sequence import PolynomialSequence
import re
import pdb

In [2]:
# It’s possible to compile code in a notebook cell with Cython. For this you need to load the Cython magic:
# Then you can define a Cython cell by writing %%cython on top of it. Like this:
# %%cython
# cython codes
%load_ext cython

In [3]:
%%cython -I ./

from libc.stdint cimport uint32_t, uint64_t
from libc.stdlib cimport malloc, calloc, free
    
cdef extern from "keeloq.c":
    void keeloq_encrypt(uint64_t *key, uint32_t *plaintext, uint32_t *ciphertext, int nrounds)
    void keeloq_decrypt(uint64_t *key, uint32_t *plaintext, uint32_t *ciphertext, int nrounds)
    
cdef extern from "polygen.c":
    ctypedef struct polynomial:
        char poly[300]
    uint64_t calculate_num_of_equations(int r, int number_of_plains)
    void polynomials(uint32_t *plains, uint32_t *ciphers, polynomial *equations, int r, int number_of_plains)

def keeloq_enc(k, p, r):
    cdef uint64_t k1
    cdef uint32_t p1
    cdef uint32_t c1
    k1, p1 = k, p
    keeloq_encrypt(&k1, &p1, &c1, r)
    return c1

def keeloq_dec(k, c, r):
    cdef:
        uint64_t k1
        uint32_t p1
        uint32_t c1
    k1, c1 = k, c
    keeloq_decrypt(&k1, &p1, &c1, r)
    return p1
    
def keeloq_polys(ptexts, ctexts, r):
    cdef:
        int number_of_plaintexts = len(ptexts)
        uint64_t neqs        
        uint32_t *plains = <uint32_t *> calloc(number_of_plaintexts, sizeof(uint32_t))
        uint32_t *ciphers = <uint32_t *> calloc(number_of_plaintexts, sizeof(uint32_t))
        polynomial *equations
        
    for i in range(number_of_plaintexts):
        plains[i] = ptexts[i]
        ciphers[i] = ctexts[i]
    neqs = calculate_num_of_equations(r, number_of_plaintexts)
    equations = <polynomial *>malloc(neqs * sizeof(polynomial))
    polynomials(plains, ciphers, equations, r, number_of_plaintexts)
    free(plains)
    free(ciphers)
    st = []
    for i in range(neqs):
        st.append(equations[i].poly)
    free(equations)
    return st

In [4]:
k = 0x5cec6701b79fd949
p = 0xf741e2db
r = 528
c = keeloq_enc(k, p, r)
hex(c)

'0xe44f4cdf'

In [5]:
@parallel
def paralle_encrypt(k, p, r):
    return keeloq_enc(k, p, r)

In [13]:
def serial_encrypt(k, p, r):
    ciphers = []
    for p in plains:
        temp = ciphers.append(keeloq_enc(k, p, r))
        
    return ciphers

In [14]:
r = 528
k = 0x5cec6701b79fd949
number_of_plains = 2^3
plains = [randint(0, 2^32 - 1) for _ in range(number_of_plains)]
inputs = [(k, plains[i], r) for i in range(len(plains))]

In [18]:
%time ciphers = paralle_encrypt(inputs)

CPU times: user 11 µs, sys: 0 ns, total: 11 µs
Wall time: 12.4 µs


In [19]:
%time ciphers = serial_encrypt(k, plains, r)

CPU times: user 72 µs, sys: 10 µs, total: 82 µs
Wall time: 86.1 µs


In [20]:
k = 0x5cec6701b79fd949
r = 128
number_of_plains = 2
plains = [randint(0, 2^32 - 1) for _ in range(number_of_plains)]
ciphers = [0]*number_of_plains
for i in range(number_of_plains):
    ciphers[i] = keeloq_enc(k, plains[i], r)
%time temp = keeloq_polys(plains, ciphers, r)
vrs = []
equations = []
for f in temp:
    f = f.decode('utf-8')
    equations.append(f)
    terms = re.split(r' \+ |\*', f)
    for v in terms:
        if (not v.isdigit()):
            vrs.append(v)
vrs = list(set(vrs))
R = BooleanPolynomialRing(len(vrs), vrs)
%time ps = list(map(R, equations))
ps = PolynomialSequence(ps)

CPU times: user 697 µs, sys: 105 µs, total: 802 µs
Wall time: 805 µs
CPU times: user 25.5 ms, sys: 0 ns, total: 25.5 ms
Wall time: 25 ms


In [21]:
ps

Polynomial Sequence with 896 Polynomials in 896 Variables

In [12]:
# %time sls = solve_sat(ps, n = infinity, s_verbosity = 4, solver=sage.sat.solvers.cryptominisat.CryptoMiniSat)
# # print(sls)
# print("number of solutions : %d" % len(sls))

In [22]:
def guss_keys(ps, ng, original_key):
    original_key = bin(original_key)[2:].zfill(64)
    original_key = list(original_key)
    original_key.reverse()
    original_key = list(map(R, original_key))
    gps = []
    for p in ps:
        gps.append(p)
    for i in range(ng):
        temp = "k_%d + %d" % (i, original_key[i])
        temp = R(temp)
        gps.append(temp)
    return PolynomialSequence(gps)

In [23]:
k = 0x5cec6701b79fd949
gps = guss_keys(ps, 30, k)
print(ps)
print(gps)

Polynomial Sequence with 896 Polynomials in 896 Variables
Polynomial Sequence with 926 Polynomials in 896 Variables


In [15]:
%time sls = solve_sat(gps, n = infinity, s_verbosity = 4)
#print(sls)
print("number of solutions : %d" % len(sls))

c clause size stats. size3: 2282 size4: 12632 size5: 0 larger: 0
c [find&init matx] performing matrix init
c [xor-rem-unconnected] left with 190 xors from 190 non-empty xors T: 0.00
c xor after clean: 165 + 262 + 402 + 1247 + 1248 =  false -- clash: 1255, 1256, 1257, 1258, 1259, 1260, 
c xor after clean: 202 + 214 + 529 + 1261 + 1262 + 1264 =  false -- clash: 1269, 1270, 1271, 1272, 1273, 1274, 
c xor after clean: 659 + 709 + 1277 =  false -- clash: 1283, 1284, 1285, 1286, 1287, 1288, 
c xor after clean: 300 + 426 + 643 + 1289 + 1291 + 1292 + 1293 + 1295 =  true -- clash: 1297, 1298, 1299, 1300, 1301, 1302, 
c xor after clean: 142 + 260 + 497 + 1306 + 1309 =  false -- clash: 1311, 1312, 1313, 1314, 1315, 1316, 
c xor after clean: 291 + 297 + 1321 =  true -- clash: 1325, 1326, 1327, 1328, 1329, 1330, 
c xor after clean: 114 + 308 + 650 + 1331 + 1333 + 1337 =  false -- clash: 1339, 1340, 1341, 1342, 1343, 1344, 
c xor after clean: 153 + 804 + 1346 + 1348 + 1349 =  false -- clash: 1353, 1

c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 1338/1927 cl-short:1338 lit-r:1874 T: 0.02 T-out: Y T-r: -0.06%
c [restart] at confl 7625 -- adjusting local restart type: geometric  budget: 233       maple step_size: 0.4000 branching: vsid   decay: 0.8100
c [restart] at confl 7860 -- adjusting local restart type: glue       budget: 1165      maple step_size: 0.4000 branching: vsid   decay: 0.8100
c glue auto  vsx    54  8193    2577 14914  4803    3.85    3.40   401  2096  5593   101   19.25   19.04
c [restart] at confl 9026 -- adjusting local restart type: geometric  budget: 256       maple step_size: 0.40 branching: vsid   decay: 0.8200
c [restart] at confl 9283 -- adjusting local restart type: glue       budget: 1280      maple step_size: 0.4000 branching: vsid   decay: 0.8200
c [DBclean lev1] confl: 10002 orig size: 2348 used recently: 723 not used recently: 0 moved w0: 1625 T: 0.00
c [restart] at confl 10564 -- adjusting local restart

c [restart] at confl 63656 -- adjusting local restart type: geometric  budget: 1158      maple step_size: 0.40 branching: vsid   decay: 0.9500
c [distill] long cls tried: 423/5460 cl-short:422 lit-r:237 T: 0.05 T-out: N T-r: 97.80%
c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 36/4491 cl-short:35 lit-r:38 T: 0.01 T-out: Y T-r: -4.01%
c [restart] at confl 64817 -- adjusting local restart type: glue       budget: 5790      maple step_size: 0.4000 branching: vsid   decay: 0.9500
c glue auto  vsx   141   65K    2577 14914  4803    3.85    3.40  5461  4556   38K   108   18.57   18.53
c Over limit of conflicts for this restart -- restarting as soon as possible!
c search over max conflicts
c Searcher::solve() finished status: l_Undef numConflicts : 70001 SumConfl: 70001 max_confl_per_search_solve_call:70000
c ------ THIS ITERATION SOLVING STATS -------
c restarts                 : 141         (496.46    confls per restart)
c blocked restarts   

c --> Executing strategy token: distill-cls
c [distill] long cls tried: 6959/6786 cl-short:1446 lit-r:639 T: 0.10 T-out: N T-r: 47.69%
c -------- DISTILL STATS --------
c time                     : 0.20        (0.10      per call)
c timed out                : 0           (0.00      % of calls)
c distill/checked/potential: 2892       /13918/13918
c lits-rem                 : 1278        
c 0-depth-assigns          : 8           (0.19      % of vars)
c -------- DISTILL STATS END --------
c --> Executing strategy token: scc-vrepl
c ----- SCC STATS --------
c time                     : 0.00        (0.00      per call)
c called                   : 1           (97.00     new found per call)
c found                    : 97          (53.30     % of all found)
c bogoprops                : 34589       % of all found
c ----- SCC STATS END --------
c [clean] T: 0.00
c --------- VAR REPLACE STATS ----------
c time                     : 0.01        (0.01      per call)
c trees' crown             : 9

c x n vars       : 555
c another run ?
Eliminated clause -719 -1506 -1861 1862 (red: 0) on var 1862
Eliminated clause 50 -1861 1862 (red: 0) on var 1862
Eliminated clause -50 -609 -719 -1506 1862 (red: 0) on var 1862
Eliminated clause 50 1506 -1856 1862 (red: 0) on var 1862
Eliminated clause -1862 719 (red: 0) on var 1862
Eliminated clause -1862 1856 (red: 0) on var 1862
Eliminated clause -1862 609 (red: 1) on var 1862
Eliminated clause 50 1861 -1862 (red: 0) on var 1862
Eliminated clause -1506 1861 -1862 (red: 0) on var 1862
Eliminated clause 50 -1506 -1862 (red: 0) on var 1862
Eliminated clause -50 1506 -1862 (red: 0) on var 1862
Eliminated clause 549 -888 1988 -2246 (red: 0) on var 1988
Eliminated clause -549 -737 -888 1988 (red: 0) on var 1988
Eliminated clause 460 -1979 1987 1988 (red: 0) on var 1988
Eliminated clause -460 -888 1979 1987 1988 (red: 0) on var 1988
Eliminated clause -460 -888 -1979 -1987 1988 (red: 0) on var 1988
Eliminated clause 460 1979 -1987 1988 (red: 0) on var

...

c [restart] at confl 4429543 -- adjusting local restart type: luby       budget: 800       maple step_size: 0.0600 branching: mapl   decay: 0.9000
c [restart] at confl 4430344 -- adjusting local restart type: luby       budget: 100       maple step_size: 0.0600 branching: mapl   decay: 0.9000
c [distill] long cls tried: 68/46068 cl-short:67 lit-r:5 T: 0.01 T-out: N T-r: 99.62%
c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 31/5264 cl-short:31 lit-r:4 T: 0.01 T-out: Y T-r: -3.17%
c [DBclean lev1] confl: 4430365 orig size: 5264 used recently: 5009 not used recently: 197 moved w0: 58 T: 0.00
c [restart] at confl 4430445 -- adjusting local restart type: luby       budget: 100       maple step_size: 0.0600 branching: mapl   decay: 0.9000
c [restart] at confl 4430546 -- adjusting local restart type: luby       budget: 200       maple step_size: 0.0600 branching: mapl   decay: 0.9000
c [restart] at confl 4430750 -- adjusting local restart type: 

c [occ-sub-long-w-long] rem cl: 78 tried: 65406/99697 (65.6%) T: 0.12 T-out: Y T-r: -0.00%
c [occ-sub-str-long-w-long] sub: 38 str: 77 tried: 148158/99697 (148.6)  T: 0.30 T-out: Y T-r: -0.00%
c --> Executing OCC strategy token: occ-clean-implicit
c --> Executing OCC strategy token: occ-bve
c [occ-empty-res] Empty resolvent elimed: 0 T: 0.00 T-out: N
c x n vars       : 364
c size of added_cl_to_var    : 0
c size of removed_cl_with_var: 0
c x n vars       : 364
c another run ?
c [occ-bve] iter v-elim 0
c cl_inc_rate=1.0, var_dec_rate=1.0 (grow=0)
c Reduced to 364 vars, 6220 cls (grow=0)
c x n vars       : 364
c size of added_cl_to_var    : 0
c size of removed_cl_with_var: 0
c x n vars       : 364
c another run ?
c [occ-bve] iter v-elim 0
c cl_inc_rate=1.0, var_dec_rate=1.0 (grow=8)
c Reduced to 364 vars, 6220 cls (grow=8)
c x n vars       : 364
c size of added_cl_to_var    : 0
c size of removed_cl_with_var: 0
c x n vars       : 364
c another run ?
c [occ-bve] iter v-elim 0
c cl_inc_rate

c [distill] long cls tried: 221/46190 cl-short:208 lit-r:7 T: 0.04 T-out: N T-r: 98.31%
c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 19/7067 cl-short:19 lit-r:4 T: 0.01 T-out: Y T-r: -4.92%
c [restart] at confl 4444091 -- adjusting local restart type: glue       budget: 550       maple step_size: 0.0600 branching: vsid   decay: 0.9900
c [restart] at confl 4444642 -- adjusting local restart type: geometric  budget: 121       maple step_size: 0.0600 branching: vsid   decay: 0.9900
c [restart] at confl 4444765 -- adjusting local restart type: glue       budget: 605       maple step_size: 0.0600 branching: vsid   decay: 0.9900
c [g  <0] Disabling GJ-elim in this round.  Usefulness was: 0.0814%  over 7368 calls
c [restart] at confl 4445373 -- adjusting local restart type: geometric  budget: 133       maple step_size: 0.06 branching: vsid   decay: 0.9900
c [restart] at confl 4445508 -- adjusting local restart type: glue       budget: 665     

c [DBclean lev2] confl: 4485216 orig size: 53770 marked: 23658 ttl:15116 locked_solver:1 T: 0.00
c [mem] consolidate  old-sz: 9515K new-sz: 7005K new bits offs: 20 T: 0.00
c [restart] at confl 4485491 -- adjusting local restart type: geometric  budget: 792       maple step_size: 0.06 branching: vsid   decay: 0.9900
c [restart] at confl 4486285 -- adjusting local restart type: glue       budget: 3960      maple step_size: 0.0600 branching: vsid   decay: 0.9900
c glue auto  vs2  6588 4489K     364  6206    14    4.63    4.63   46K  6902   43K     2   12.39   12.38
c [restart] at confl 4490247 -- adjusting local restart type: geometric  budget: 871       maple step_size: 0.06 branching: vsid   decay: 0.9900
c [distill] long cls tried: 157/46519 cl-short:157 lit-r:63 T: 0.04 T-out: N T-r: 98.55%
c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 79/6921 cl-short:79 lit-r:21 T: 0.01 T-out: Y T-r: -2.38%
c [DBclean lev1] confl: 4490367 orig size: 6

c [DBclean lev2] confl: 4575227 orig size: 49910 marked: 21960 ttl:12816 locked_solver:5 T: 0.00
c [mem] consolidate  old-sz: 9410K new-sz: 7177K new bits offs: 20 T: 0.00
c [restart] at confl 4575684 -- adjusting local restart type: glue       budget: 11265     maple step_size: 0.06 branching: vsid   decay: 0.9900
c glue auto  vs2  6611 4579K     364  6206    14    4.63    4.63   48K 16387   38K    70   11.45   11.44
c [DBclean lev1] confl: 4580373 orig size: 16430 used recently: 14769 not used recently: 1200 moved w0: 461 T: 0.00
c [restart] at confl 4586951 -- adjusting local restart type: geometric  budget: 2478      maple step_size: 0.06 branching: vsid   decay: 0.9900
c [distill] long cls tried: 632/48923 cl-short:438 lit-r:874 T: 0.11 T-out: N T-r: 96.29%
c Need to finish distillation -- ran out of prop (=allocated time)
c [distill] long cls tried: 52/16417 cl-short:33 lit-r:73 T: 0.01 T-out: Y T-r: -0.59%
c geom auto  vs2  6612 4588K     363  6206    14    4.63    4.63   48K 16

In [20]:
def check_correctness(sls, original_key):
    original_key = bin(original_key)[2:].zfill(64)
    original_key = list(original_key)
    original_key.reverse()
    for n in range(0, len(sls)):
        matching_flag = True
        key_sol = dict()
        kindex = []
        for i in range(64):
            kname = 'k_%d' % i
            if kname in R.variable_names():
                kname = R(kname)
                kval = sls[n].get(kname)
                if kval != None:
                    kindex.append(i)
                    key_sol[kname] = kval        
        for i in kindex:
            if original_key[i] != str(key_sol[R("k_%d" % i)]):
                matching_flag = False
                break
        #pdb.set_trace()
        if matching_flag == True:
            print("C0ngratulati0ns! sls[%d] matches the original key :)" % n)
            print("Number of recoverd key bits: %d" % len(list(key_sol)))
            print(key_sol)
            return
    print("There is no solution matching the original key :(")

In [21]:
check_correctness(sls, k)

C0ngratulati0ns! sls[0] matches the original key :)
Number of recoverd key bits: 64
{k_0: 1, k_1: 0, k_2: 0, k_3: 1, k_4: 0, k_5: 0, k_6: 1, k_7: 0, k_8: 1, k_9: 0, k_10: 0, k_11: 1, k_12: 1, k_13: 0, k_14: 1, k_15: 1, k_16: 1, k_17: 1, k_18: 1, k_19: 1, k_20: 1, k_21: 0, k_22: 0, k_23: 1, k_24: 1, k_25: 1, k_26: 1, k_27: 0, k_28: 1, k_29: 1, k_30: 0, k_31: 1, k_32: 1, k_33: 0, k_34: 0, k_35: 0, k_36: 0, k_37: 0, k_38: 0, k_39: 0, k_40: 1, k_41: 1, k_42: 1, k_43: 0, k_44: 0, k_45: 1, k_46: 1, k_47: 0, k_48: 0, k_49: 0, k_50: 1, k_51: 1, k_52: 0, k_53: 1, k_54: 1, k_55: 1, k_56: 0, k_57: 0, k_58: 1, k_59: 1, k_60: 1, k_61: 0, k_62: 1, k_63: 0}
